In [ ]:
from google.colab import files
files.upload() #upload kaggle.json

Saving kaggle.json to kaggle.json


{'kaggle.json': b'{"username":"bazifrasool","key":"78f6f0b250077352867e8ce56974adfa"}'}

In [ ]:
!pip install -q kaggle
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
!ls ~/.kaggle
!chmod 600 /root/.kaggle/kaggle.json

kaggle.json


In [ ]:
!kaggle datasets download -d puneet6060/intel-image-classification

 97% 335M/346M [00:03<00:00, 76.6MB/s]
100% 346M/346M [00:03<00:00, 92.3MB/s]


In [ ]:
!unzip -q /content/intel-image-classification.zip 

In [ ]:
import keras
from keras.models import Sequential
from keras.layers import Dense
from keras.preprocessing.image import ImageDataGenerator
largenet_model= keras.applications.NASNetLarge(input_shape=(331, 331, 3),include_top=False,weights="imagenet",pooling="avg",classes=6)
largenet_model.summary()
model = Sequential()

343613440/343610240 [==============================] - 5s 0us/step
Model: "NASNet"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, 331, 331, 3) 0                                            
__________________________________________________________________________________________________
stem_conv1 (Conv2D)             (None, 165, 165, 96) 2592        input_1[0][0]                    
__________________________________________________________________________________________________
stem_bn1 (BatchNormalization)   (None, 165, 165, 96) 384         stem_conv1[0][0]                 
__________________________________________________________________________________________________
activation (Activation)         (None, 165, 165, 96) 0           stem_bn1[0][0]                   
__________________________

In [ ]:
from keras.models import Model
from keras.layers import Flatten
for i,each in enumerate(largenet_model.layers):
  if(i+20<len(largenet_model.layers)):
    each.trainable=False
#mdl=Model(largenet_model)
#mdl.add(Dense(6,activation="softmax"))
flattened = Flatten()(largenet_model.output)
fc2 = Dense(6, activation='softmax')(flattened)
model = Model(inputs=largenet_model.input, outputs=fc2)


In [ ]:
keras.utils.plot_model(model, "my_first_model.png")

In [ ]:
model.compile(optimizer="adam",loss = "categorical_crossentropy",metrics=["accuracy"])
classifier=model
train_datagen = ImageDataGenerator(
        rescale=1./255,
        shear_range=0.2,
        zoom_range=0.2,
        horizontal_flip=True)

test_datagen = ImageDataGenerator(rescale=1./255)

training_set= train_datagen.flow_from_directory(
        './seg_train/seg_train',
        target_size=(331,331),
        batch_size=64)

test_set = test_datagen.flow_from_directory(
        './seg_test/seg_test',
        target_size=(331,331),
        batch_size=64)

classifier.fit(
        training_set,
        steps_per_epoch=14034//64,
        epochs=20,
        validation_data=test_set,
        validation_steps=3000//64)

Found 14034 images belonging to 6 classes.
Found 3000 images belonging to 6 classes.
Epoch 1/20
219/219 [==============================] - 560s 3s/step - loss: 0.2430 - accuracy: 0.9092 - val_loss: 0.6721 - val_accuracy: 0.8781
Epoch 2/20
219/219 [==============================] - 542s 2s/step - loss: 0.1866 - accuracy: 0.9301 - val_loss: 0.9017 - val_accuracy: 0.8607
Epoch 3/20
219/219 [==============================] - 536s 2s/step - loss: 0.1666 - accuracy: 0.9366 - val_loss: 0.6879 - val_accuracy: 0.8944
Epoch 4/20
219/219 [==============================] - 539s 2s/step - loss: 0.1486 - accuracy: 0.9436 - val_loss: 0.5761 - val_accuracy: 0.9049
Epoch 5/20
219/219 [==============================] - 545s 2s/step - loss: 0.1396 - accuracy: 0.9460 - val_loss: 0.4959 - val_accuracy: 0.9076
Epoch 6/20
219/219 [==============================] - 544s 2s/step - loss: 0.1284 - accuracy: 0.9497 - val_loss: 0.6242 - val_accuracy: 0.8930
Epoch 7/20
219/219 [==============================] - 539

In [ ]:
model.save("./IntelSceneRecognition_NASnet.h5")